# Data 643 Project 2 : Attempt

In [1]:
import graphlab
import numpy as np
import pandas as pd
from urllib2 import *
from IPython.display import display
from IPython.display import Image
graphlab.canvas.set_target('ipynb')


## This is my attempt to learn python; switching from R; while completing Project 2. 

In [2]:
preference = pd.read_csv('ratings.csv')
movies = pd.read_csv('movies.csv')
#It is important to note, I am using experimental movieLens dataset, containing only the latest movies made.

In [3]:
preference.columns

Index([u'userId', u'movieId', u'rating', u'timestamp'], dtype='object')

In [4]:
preference.rename(columns={'userId':'user_id','movieId':'item_id'},inplace=True)
preference.drop('timestamp',axis=1, inplace=True)

movies.rename(columns={'movieId':'item_id'},inplace=True)
movies.loc[movies['item_id'] == 3070]

item_id                                              title  \
2467     3070  Adventures of Buckaroo Banzai Across the 8th D...   

                       genres  
2467  Adventure|Comedy|Sci-Fi

## Graphlab prefers long format data for their SFrames; I make training and testing sets below.

In [5]:
data = preference.merge(movies, on='item_id')
data_SFrame = graphlab.SFrame(data)
training_data_SFrame, testing_data_SFrame = data_SFrame.random_split(.8,seed=5)




training_data_SFrame.show()
testing_data_SFrame.show()

[INFO] graphlab.cython.cy_server: GraphLab Create v2.1 started. Logging: C:\Users\Exped\AppData\Local\Temp\graphlab_server_1497834577.log.0


This non-commercial license of GraphLab Create for academic use is assigned to Michael.Muller@spsmail.cuny.edu and will expire on June 06, 2018.


## I include a facorization model to see how it does against item-item and user-user recommender models. No validation, just a quick glance; takes about 4 seconds to run. RMSE is very low.

In [6]:
factorizationModel = graphlab.recommender.create(training_data_SFrame,user_id='user_id',item_id='item_id',target='rating',ranking=False)

Recsys training: model = factorization_recommender

Preparing data set.

Data has 80037 observations with 671 users and 8306 items.

Data prepared in: 0.094137s

Training factorization_recommender for recommendations.

...

+---------+--------------+-------------------+-----------------------+-------------+

Optimization Complete: Maximum number of passes through the data reached.

Computing final objective value and training RMSE.

Final objective value: 0.264254

Final training RMSE: 0.513961

## I make two models on training data; item-item based with cosine similarity measure and jaccard. Jaccard takes slightly less longer to complete.

In [7]:
item_item_model_cosine = graphlab.recommender.item_similarity_recommender.create(training_data_SFrame,user_id='user_id',item_id='item_id',target='rating',similarity_type='cosine')
item_item_model_jaccard = graphlab.recommender.item_similarity_recommender.create(training_data_SFrame,user_id='user_id',item_id='item_id',target='rating',similarity_type='jaccard')

Recsys training: model = item_similarity

Warning: Ignoring columns title, genres;

To use these columns in scoring predictions, use a model that allows the use of additional features.

Preparing data set.

Data has 80037 observations with 671 users and 8306 items.

...

| 70.603ms                            | 0                | 0               |

| 445.644ms                           | 100              | 8306            |

+-------------------------------------+------------------+-----------------+

Finalizing lookup tables.

Generating candidate set for working with new users.

In [8]:
rec_jac = item_item_model_jaccard.recommend()
rec_cos = item_item_model_cosine.recommend()


Finished training in 0.453655s

In [12]:
performance = graphlab.compare(testing_data_SFrame,[item_item_model_jaccard,item_item_model_cosine])
graphlab.show_comparison(performance,[item_item_model_jaccard,item_item_model_cosine])

PROGRESS: Evaluate model M0

Precision and recall summary statistics by cutoff
+--------+----------------+-----------------+
| cutoff | mean_precision |   mean_recall   |
+--------+----------------+-----------------+
|   1    | 0.269058295964 | 0.0192763918736 |
|   2    | 0.265321375187 | 0.0366613244226 |
|   3    | 0.253612356751 | 0.0499009712822 |
|   4    | 0.246263079223 | 0.0629974089237 |
|   5    | 0.240657698057 |  0.078031264142 |
|   6    | 0.232685600399 | 0.0899537532473 |
|   7    | 0.227845398249 |  0.101025200286 |
|   8    | 0.221786248132 |  0.111483520289 |
|   9    | 0.218734429497 |  0.12051767779  |
|   10   | 0.214050822123 |  0.128965096761 |
+--------+----------------+-----------------+
[10 rows x 3 columns]

PROGRESS: Evaluate model M1

Precision and recall summary statistics by cutoff
+--------+----------------+-----------------+
| cutoff | mean_precision |   mean_recall   |
+--------+----------------+-----------------+
|   1    | 0.346786248132 | 0.0266669

In [10]:
m = graphlab.recommender.item_content_recommender.create(training_data_SFrame, "item_id",user_id='user_id')

('Applying transform:\n', Class             : AutoVectorizer

Model Fields
------------
Features          : ['user_id', 'rating', 'title', 'genres']
Excluded Features : ['item_id']

Column   Type   Interpretation  Transforms                         Output Type
-------  -----  --------------  ---------------------------------  -----------
user_id  int    numerical       None                               int        
rating   float  numerical       None                               float      
title    str    short_text      3-Character NGram Counts -> TFIDF  dict       
genres   str    categorical     None                               str        

)


Recsys training: model = item_content_recommender

Defaulting to brute force instead of ball tree because there are multiple distance components.


Starting brute force nearest neighbors model training.

Starting pairwise querying.

...

Data has 0 observations with 0 users and 8306 items.

Data prepared in: 4.37241s

Loading user-provided nearest items.

Generating candidate set for working with new users.

Finished training in 0.093135s

## Looks like cosine similarity is the best way to go from the two item-item recommendation algorithims. Slightly less time, for significantly better results. Factorization algorithim was a bit too high level for this exercise, and the user-user recommendation algorithim was 'experimental', and either I did not read its documentation right; or it errored.